In [1]:
from utils.general_utils import PreprocessingUtils
from cb_config import *
from cb_utilities import cb_calculate_system_costs, cb_calculate_transformation_costs,cb_process_interactions
from data_reader import CBFilesReader
from cb_config import * 
import pickle

from typing import List
import pandas as pd 
import os 
import re 
import numpy as np
from new_strategies import strategy_list, strategy_dict

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
country_id = 'iran'
attr_primary_file_name = "ATTRIBUTE_PRIMARY_new.csv"
attr_strategy_file_name = "ATTRIBUTE_STRATEGY_new.csv"
ssp_output_data_file_name = "ssp_output_data.csv"
comparison_strategy_code = "BASE"
transformation_names_url = "https://github.com/jcsyme/sisepuede/blob/main/sisepuede/attributes/attribute_transformer_code.csv"

In [4]:
# Create an instance of utilities
p_utils = PreprocessingUtils()

In [5]:
## ----------- DEFINE PATHS  ----------- ##
CB_DIR_PATH = p_utils.build_path([os.getcwd(), ".."])
CB_DATA_PATH = p_utils.build_path([CB_DIR_PATH, "cb_data"])
STRATEGY_SPECIFIC_CB_PATH_FILES = p_utils.build_path([CB_DATA_PATH, "strategy_specific_cb_files"])
SSP_RESULTS_DATA_PATH = p_utils.build_path([CB_DIR_PATH, "ssp_output_data", f"{country_id}_data"])
DEFINITION_FILES_PATH = p_utils.build_path([CB_DATA_PATH, "definition_files"])
STRATEGY_DEFINITION_FILE_PATH = p_utils.build_path([SSP_RESULTS_DATA_PATH, attr_strategy_file_name])
CB_OUTPUT_PATH = p_utils.build_path([CB_DIR_PATH, "cb_output"])
DEBUG_DIR_PATH = p_utils.build_path([CB_DIR_PATH, "src","debug"])
data_filename = p_utils.build_path([SSP_RESULTS_DATA_PATH, ssp_output_data_file_name] )
primary_filename = p_utils.build_path([SSP_RESULTS_DATA_PATH, attr_primary_file_name])
strategy_filename = p_utils.build_path([SSP_RESULTS_DATA_PATH, attr_strategy_file_name])

In [6]:
# Opening definition files

#the list of all the cost factor files in the system, and the functions they should be evaluated with
cost_factor_names = pd.read_csv(p_utils.build_path([DEFINITION_FILES_PATH, 'system_cost_factors_list.csv']))  

#defines how each transformation is evaluated, including difference variables, cost multipliers, etc.
transformation_cost_definitions = pd.read_csv(p_utils.build_path([DEFINITION_FILES_PATH, 'transformation_cost_definitions.csv']), encoding="latin")

#calculate system costs
cb_data = CBFilesReader(CB_DATA_PATH)

In [7]:
# Read ssp output file
ssp_output_df = pd.read_csv(data_filename)
ssp_output_df.head()

primary_id region  time_period  area_agrc_crops_bevs_and_spices  \
0           0   iran            0                     2.171328e+06   
1           0   iran            1                     2.202367e+06   
2           0   iran            2                     2.187993e+06   
3           0   iran            3                     2.210508e+06   
4           0   iran            4                     2.326647e+06   

   area_agrc_crops_cereals  area_agrc_crops_fibers  area_agrc_crops_fruits  \
0             4.829814e+06            1.002152e+06            2.612089e+06   
1             4.898855e+06            1.016477e+06            2.649429e+06   
2             4.866883e+06            1.009843e+06            2.632137e+06   
3             4.916964e+06            1.020235e+06            2.659223e+06   
4             5.175298e+06            1.073837e+06            2.798936e+06   

   area_agrc_crops_herbs_and_other_perennial_crops  area_agrc_crops_nuts  \
0                                     3.370662e+06          1.839598e+06   
1                                     3.418845e+06          1.865894e+06   
2                                     3.396532e+06          1.853717e+06   
3                                     3.431484e+06          1.872792e+06   
4                                     3.611771e+06          1.971187e+06   

   area_agrc_crops_other_annual  ...  yf_agrc_fruits_tonne_ha  \
0                  2.433465e+06  ...                      0.0   
1                  2.468251e+06  ...                      0.0   
2                  2.452142e+06  ...                      0.0   
3                  2.477375e+06  ...                      0.0   
4                  2.607535e+06  ...                      0.0   

   yf_agrc_herbs_and_other_perennial_crops_tonne_ha  yf_agrc_nuts_tonne_ha  \
0                                               0.0                    0.0   
1                                               0.0                    0.0   
2                                               0.0                    0.0   
3                                               0.0                    0.0   
4                                               0.0                    0.0   

   yf_agrc_other_annual_tonne_ha  yf_agrc_other_woody_perennial_tonne_ha  \
0                            0.0                                     0.0   
1                            0.0                                     0.0   
2                            0.0                                     0.0   
3                            0.0                                     0.0   
4                            0.0                                     0.0   

   yf_agrc_pulses_tonne_ha  yf_agrc_rice_tonne_ha  \
0                      0.0               3.954868   
1                      0.0               3.954868   
2                      0.0               3.954868   
3                      0.0               3.954868   
4                      0.0               3.954868   

   yf_agrc_sugar_cane_tonne_ha  yf_agrc_tubers_tonne_ha  \
0                          0.0                18.243230   
1                          0.0                16.534650   
2                          0.0                11.059807   
3                          0.0                15.064940   
4                          0.0                20.334864   

   yf_agrc_vegetables_and_vines_tonne_ha  
0                             249.320740  
1                             243.143417  
2                             222.736440  
3                             232.339302  
4                             212.567344  

[5 rows x 3669 columns]

In [8]:
# Merge ATTRIBUTE_STRATEGY and ATTRIBUTE_PRIMARY by strategy_code
merged_attr_df = p_utils.merge_attribute_files(primary_filename, strategy_filename)
merged_attr_df.head()


primary_id  design_id  strategy_id  future_id  \
0           0          0            0          0   
1       77077          0         7001          0   
2       78078          0         7002          0   
3       79079          0         7003          0   
4       80080          0         7004          0   

                               strategy_code  \
0                                       BASE   
1                  TORNADO:AGRC:DEC_CH4_RICE   
2                   TORNADO:AGRC:DEC_EXPORTS   
3       TORNADO:AGRC:DEC_LOSSES_SUPPLY_CHAIN   
4  TORNADO:AGRC:INC_CONSERVATION_AGRICULTURE   

                                    strategy description  \
0                           Strategy TX:BASE         NaN   
1                  TORNADO:AGRC:DEC_CH4_RICE         NaN   
2                   TORNADO:AGRC:DEC_EXPORTS         NaN   
3       TORNADO:AGRC:DEC_LOSSES_SUPPLY_CHAIN         NaN   
4  TORNADO:AGRC:INC_CONSERVATION_AGRICULTURE         NaN   

                        transformation_specification  baseline_strategy_id  
0                                            TX:BASE                     1  
1                  TX:AGRC:DEC_CH4_RICE|TX:LNDU:PLUR                     0  
2                   TX:AGRC:DEC_EXPORTS|TX:LNDU:PLUR                     0  
3       TX:AGRC:DEC_LOSSES_SUPPLY_CHAIN|TX:LNDU:PLUR                     0  
4  TX:AGRC:INC_CONSERVATION_AGRICULTURE|TX:LNDU:PLUR                     0

In [9]:
merged_attr_df_clean = p_utils.remove_suffix_from_transformations(merged_attr_df)

In [10]:
# Check if the suffix elimnation works
filtered_df = merged_attr_df_clean[merged_attr_df_clean.strategy_code.str.endswith('HIGHEST', na=False)]
filtered_df[['strategy_code', 'transformation_specification']]

strategy_code  \
12    TORNADO:INEN:INC_EFFICIENCY_ENERGY_HIGHEST   
17                 TORNADO:IPPU:DEC_HFCS_HIGHEST   
37         TORNADO:SOIL:DEC_LIME_APPLIED_HIGHEST   
38            TORNADO:SOIL:DEC_N_APPLIED_HIGHEST   
55  TORNADO:WASO:DEC_CONSUMER_FOOD_WASTE_HIGHEST   

                    transformation_specification  
12    TX:INEN:INC_EFFICIENCY_ENERGY|TX:LNDU:PLUR  
17                 TX:IPPU:DEC_HFCS|TX:LNDU:PLUR  
37         TX:SOIL:DEC_LIME_APPLIED|TX:LNDU:PLUR  
38            TX:SOIL:DEC_N_APPLIED|TX:LNDU:PLUR  
55  TX:WASO:DEC_CONSUMER_FOOD_WASTE|TX:LNDU:PLUR

In [11]:
p_utils.check_missing_transformations(merged_attr_df_clean, transformation_cost_definitions)

The following transformations are not in the transformation_cost_definitions file. Please update it to avoid affecting the calculation of transformation costs:
 {'TX:SOIL:DEC_LIME_APPLIED', 'TX:WASO:INC_CAPTURE_BIOGAS', 'TX:TRNS:INC_OCCUPANCY_LIGHT_DUTY', 'TX:WASO:INC_ENERGY_FROM_BIOGAS', 'TX:LVST:DEC_EXPORTS', 'TX:TRWW:INC_CAPTURE_BIOGAS', 'TX:WASO:INC_ENERGY_FROM_INCINERATION', 'TX:WASO:INC_RECYCLING', 'TX:ENTC:TARGET_CLEAN_HYDROGEN', 'TX:TRNS:SHIFT_MODE_REGIONAL', 'TX:WALI:INC_TREATMENT_INDUSTRIAL', 'TX:LSMM:INC_CAPTURE_BIOGAS', 'TX:SOIL:DEC_N_APPLIED', 'TX:TRNS:SHIFT_MODE_PASSENGER', 'TX:TRDE:DEC_DEMAND', 'TX:LNDU:INC_REFORESTATION', 'TX:WALI:INC_TREATMENT_URBAN', 'TX:LSMM:INC_MANAGEMENT_POULTRY', 'TX:WASO:INC_LANDFILLING', 'TX:BASE', 'TX:WASO:INC_ANAEROBIC_AND_COMPOST', 'TX:INEN:INC_EFFICIENCY_PRODUCTION', 'TX:TRNS:SHIFT_MODE_FREIGHT', 'TX:LSMM:INC_MANAGEMENT_OTHER', 'TX:WALI:INC_TREATMENT_RURAL', 'TX:AGRC:DEC_EXPORTS', 'TX:LNDU:DEC_DEFORESTATION', 'TX:LNDU:PLUR', 'TX:TRWW:INC_COM

In [12]:
# Merges the attributes data with the ssp output data on primary_id
ssp_output_df_merge = merged_attr_df_clean[['primary_id', 'strategy_code', 'future_id']].merge(right = ssp_output_df, on='primary_id')
ssp_output_df_merge.head()

primary_id strategy_code  future_id region  time_period  \
0           0          BASE          0   iran            0   
1           0          BASE          0   iran            1   
2           0          BASE          0   iran            2   
3           0          BASE          0   iran            3   
4           0          BASE          0   iran            4   

   area_agrc_crops_bevs_and_spices  area_agrc_crops_cereals  \
0                     2.171328e+06             4.829814e+06   
1                     2.202367e+06             4.898855e+06   
2                     2.187993e+06             4.866883e+06   
3                     2.210508e+06             4.916964e+06   
4                     2.326647e+06             5.175298e+06   

   area_agrc_crops_fibers  area_agrc_crops_fruits  \
0            1.002152e+06            2.612089e+06   
1            1.016477e+06            2.649429e+06   
2            1.009843e+06            2.632137e+06   
3            1.020235e+06            2.659223e+06   
4            1.073837e+06            2.798936e+06   

   area_agrc_crops_herbs_and_other_perennial_crops  ...  \
0                                     3.370662e+06  ...   
1                                     3.418845e+06  ...   
2                                     3.396532e+06  ...   
3                                     3.431484e+06  ...   
4                                     3.611771e+06  ...   

   yf_agrc_fruits_tonne_ha  yf_agrc_herbs_and_other_perennial_crops_tonne_ha  \
0                      0.0                                               0.0   
1                      0.0                                               0.0   
2                      0.0                                               0.0   
3                      0.0                                               0.0   
4                      0.0                                               0.0   

   yf_agrc_nuts_tonne_ha  yf_agrc_other_annual_tonne_ha  \
0                    0.0                            0.0   
1                    0.0                            0.0   
2                    0.0                            0.0   
3                    0.0                            0.0   
4                    0.0                            0.0   

   yf_agrc_other_woody_perennial_tonne_ha  yf_agrc_pulses_tonne_ha  \
0                                     0.0                      0.0   
1                                     0.0                      0.0   
2                                     0.0                      0.0   
3                                     0.0                      0.0   
4                                     0.0                      0.0   

   yf_agrc_rice_tonne_ha  yf_agrc_sugar_cane_tonne_ha  \
0               3.954868                          0.0   
1               3.954868                          0.0   
2               3.954868                          0.0   
3               3.954868                          0.0   
4               3.954868                          0.0   

   yf_agrc_tubers_tonne_ha  yf_agrc_vegetables_and_vines_tonne_ha  
0                18.243230                             249.320740  
1                16.534650                             243.143417  
2                11.059807                             222.736440  
3                15.064940                             232.339302  
4                20.334864                             212.567344  

[5 rows x 3671 columns]

In [13]:
# Check if comparison_strategy_code exists in the ssp_output_df_merge
if not (ssp_output_df_merge.strategy_code.unique() == comparison_strategy_code).any():
    raise ValueError(f"The comparison_strategy_code '{comparison_strategy_code}' does not exist in the strategy_code column of ssp_output_df_merge.")

In [14]:
# Check if primary_id == 0 (baseline) exists in ssp_output_df_merge
if 0 not in ssp_output_df_merge['primary_id'].unique():
    raise ValueError(
        "The baseline with primary_id 0 is not present in ATTRIBUTE_PRIMARY.csv or the ssp_output_data. "
        "Please ensure it is included in both files."
    )


In [15]:
ssp_output_df_merge.shape

(2232, 3671)

In [16]:

# Removes the cols with data of furnace gas and crude (TONY: Not sure what this is about)
cols_to_keep = p_utils.get_cols_to_keep(ssp_output_df_merge.columns)
cb_input_df = ssp_output_df_merge[cols_to_keep]
print(cb_input_df.shape)


(2232, 3663)


In [17]:
# Add calculation of total TLUs to data
TLU_CONVERSION_FILE_PATH = p_utils.build_path([STRATEGY_SPECIFIC_CB_PATH_FILES, "lvst_tlu_conversions.csv"]) 
tlu_conversions_df = pd.read_csv(TLU_CONVERSION_FILE_PATH)
cb_input_df = p_utils.add_total_tlu_calculation(cb_input_df, tlu_conversions_df, cols_to_keep)
print(cb_input_df.shape)

(2232, 3664)


/home/tony/ssp/cb_ssp_refac/src/utils/general_utils.py:127: FutureWarning: The provided callable <built-in function sum> is currently using SeriesGroupBy.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "sum" instead.
  agg({"total_tlu" : sum}).\


In [18]:
cb_input_df.head()

primary_id strategy_code  future_id region  time_period  \
0           0          BASE          0   iran            0   
1           0          BASE          0   iran            1   
2           0          BASE          0   iran            2   
3           0          BASE          0   iran            3   
4           0          BASE          0   iran            4   

   area_agrc_crops_bevs_and_spices  area_agrc_crops_cereals  \
0                     2.171328e+06             4.829814e+06   
1                     2.202367e+06             4.898855e+06   
2                     2.187993e+06             4.866883e+06   
3                     2.210508e+06             4.916964e+06   
4                     2.326647e+06             5.175298e+06   

   area_agrc_crops_fibers  area_agrc_crops_fruits  \
0            1.002152e+06            2.612089e+06   
1            1.016477e+06            2.649429e+06   
2            1.009843e+06            2.632137e+06   
3            1.020235e+06            2.659223e+06   
4            1.073837e+06            2.798936e+06   

   area_agrc_crops_herbs_and_other_perennial_crops  ...  \
0                                     3.370662e+06  ...   
1                                     3.418845e+06  ...   
2                                     3.396532e+06  ...   
3                                     3.431484e+06  ...   
4                                     3.611771e+06  ...   

   yf_agrc_herbs_and_other_perennial_crops_tonne_ha  yf_agrc_nuts_tonne_ha  \
0                                               0.0                    0.0   
1                                               0.0                    0.0   
2                                               0.0                    0.0   
3                                               0.0                    0.0   
4                                               0.0                    0.0   

   yf_agrc_other_annual_tonne_ha  yf_agrc_other_woody_perennial_tonne_ha  \
0                            0.0                                     0.0   
1                            0.0                                     0.0   
2                            0.0                                     0.0   
3                            0.0                                     0.0   
4                            0.0                                     0.0   

   yf_agrc_pulses_tonne_ha  yf_agrc_rice_tonne_ha  \
0                      0.0               3.954868   
1                      0.0               3.954868   
2                      0.0               3.954868   
3                      0.0               3.954868   
4                      0.0               3.954868   

   yf_agrc_sugar_cane_tonne_ha  yf_agrc_tubers_tonne_ha  \
0                          0.0                18.243230   
1                          0.0                16.534650   
2                          0.0                11.059807   
3                          0.0                15.064940   
4                          0.0                20.334864   

   yf_agrc_vegetables_and_vines_tonne_ha  lvst_total_tlu  
0                             249.320740    1.738388e+07  
1                             243.143417    1.735076e+07  
2                             222.736440    1.736231e+07  
3                             232.339302    1.737978e+07  
4                             212.567344    1.720695e+07  

[5 rows x 3664 columns]

In [19]:
#replace any lagging references to "PFLO:SOCIOTECHNICAL" with "PFLO:CHANGE_CONSUMPTION"
cb_input_df.loc[cb_input_df["strategy_code"] == "PFLO:SOCIOTECHNICAL", "strategy_code"] = "PFLO:CHANGE_CONSUMPTION"

# Obtain SSP_GLOBAL_list_of
SSP_GLOBAL_list_of_strategies = cb_input_df["strategy_code"].unique()
SSP_GLOBAL_list_of_variables = list(set(cb_input_df.columns) - set(SSP_GLOBAL_SIMULATION_IDENTIFIERS)) # Obtains only variable names

#-------------REMOVE BASE FOR COST BENEFIT ANALYSIS------------
# data = data.query("strategy_code!='BASE'").reset_index(drop=True) # Is this necessary? 

In [20]:
#maps strategies to transformations, from James
#This file tells us which transformation in is in each strategy
strategy2tx = p_utils.build_attribute_strategy_code(transformation_names_url, SSP_GLOBAL_list_of_strategies, merged_attr_df_clean)

Successfully fetched CSV file from: https://raw.githubusercontent.com/jcsyme/sisepuede/main/sisepuede/attributes/attribute_transformer_code.csv


In [21]:
strategy2tx.head()

strategy_code  TX:AGRC:DEC_CH4_RICE  \
0                                       BASE                     0   
1                  TORNADO:AGRC:DEC_CH4_RICE                     1   
2                   TORNADO:AGRC:DEC_EXPORTS                     0   
3       TORNADO:AGRC:DEC_LOSSES_SUPPLY_CHAIN                     0   
4  TORNADO:AGRC:INC_CONSERVATION_AGRICULTURE                     0   

   TX:AGRC:DEC_DEMAND_FOR_UNHEALTHY_CROPS  TX:AGRC:DEC_EXPORTS  \
0                                       0                    0   
1                                       0                    0   
2                                       0                    1   
3                                       0                    0   
4                                       0                    0   

   TX:AGRC:DEC_LOSSES_SUPPLY_CHAIN  TX:AGRC:INC_CONSERVATION_AGRICULTURE  \
0                                0                                     0   
1                                0                                     0   
2                                0                                     0   
3                                1                                     0   
4                                0                                     1   

   TX:AGRC:INC_PRODUCTIVITY  TX:AGRC:INC_RESIDUE_REMOVAL  \
0                         0                            0   
1                         0                            0   
2                         0                            0   
3                         0                            0   
4                         0                            0   

   TX:LNDU:DEC_DEFORESTATION  TX:LNDU:DEC_DEFORESTATION_AND_INC_SILVOPASTURE  \
0                          0                                               0   
1                          0                                               0   
2                          0                                               0   
3                          0                                               0   
4                          0                                               0   

   ...  TX:TRNS:SHIFT_MODE_PASSENGER  TX:TRNS:SHIFT_MODE_REGIONAL  \
0  ...                             0                            0   
1  ...                             0                            0   
2  ...                             0                            0   
3  ...                             0                            0   
4  ...                             0                            0   

   TX:IPPU:DEC_CLINKER  TX:IPPU:DEC_DEMAND  TX:IPPU:DEC_HFCS  TX:IPPU:DEC_N2O  \
0                    0                   0                 0                0   
1                    0                   0                 0                0   
2                    0                   0                 0                0   
3                    0                   0                 0                0   
4                    0                   0                 0                0   

   TX:IPPU:DEC_OTHER_FCS  TX:IPPU:DEC_PFCS  TX:PFLO:INC_HEALTHIER_DIETS  \
0                      0                 0                            0   
1                      0                 0                            0   
2                      0                 0                            0   
3                      0                 0                            0   
4                      0                 0                            0   

   TX:PFLO:INC_IND_CCS  
0                    0  
1                    0  
2                    0  
3                    0  
4                    0  

[5 rows x 68 columns]

In [22]:
strategy2tx.to_csv(p_utils.build_path([DEBUG_DIR_PATH, 'attribute_strategy_code.csv']), index=False)

In [23]:
strategy2tx[strategy2tx.strategy_code == "TORNADO:CCSQ:INC_CAPTURE"]

strategy_code  TX:AGRC:DEC_CH4_RICE  \
6  TORNADO:CCSQ:INC_CAPTURE                     0   

   TX:AGRC:DEC_DEMAND_FOR_UNHEALTHY_CROPS  TX:AGRC:DEC_EXPORTS  \
6                                       0                    0   

   TX:AGRC:DEC_LOSSES_SUPPLY_CHAIN  TX:AGRC:INC_CONSERVATION_AGRICULTURE  \
6                                0                                     0   

   TX:AGRC:INC_PRODUCTIVITY  TX:AGRC:INC_RESIDUE_REMOVAL  \
6                         0                            0   

   TX:LNDU:DEC_DEFORESTATION  TX:LNDU:DEC_DEFORESTATION_AND_INC_SILVOPASTURE  \
6                          0                                               0   

   ...  TX:TRNS:SHIFT_MODE_PASSENGER  TX:TRNS:SHIFT_MODE_REGIONAL  \
6  ...                             0                            0   

   TX:IPPU:DEC_CLINKER  TX:IPPU:DEC_DEMAND  TX:IPPU:DEC_HFCS  TX:IPPU:DEC_N2O  \
6                    0                   0                 0                0   

   TX:IPPU:DEC_OTHER_FCS  TX:IPPU:DEC_PFCS  TX:PFLO:INC_HEALTHIER_DIETS  \
6                      0                 0                            0   

   TX:PFLO:INC_IND_CCS  
6                    0  

[1 rows x 68 columns]

In [24]:
strategy2tx[strategy2tx.strategy_code == 'TORNADO:CCSQ:INC_CAPTURE']['TX:CCSQ:INC_CAPTURE']

6    1
Name: TX:CCSQ:INC_CAPTURE, dtype: int64

In [25]:
strategy_cost_instructions = p_utils.build_strategy_cost_instructions(SSP_GLOBAL_list_of_strategies, comparison_strategy_code)
strategy_cost_instructions.to_csv(p_utils.build_path([DEBUG_DIR_PATH, 'strategy_cost_instructions.csv']), index=False)
strategy_cost_instructions.head()

strategy_code comparison_code  \
0                                       BASE            BASE   
1                  TORNADO:AGRC:DEC_CH4_RICE            BASE   
2                   TORNADO:AGRC:DEC_EXPORTS            BASE   
3       TORNADO:AGRC:DEC_LOSSES_SUPPLY_CHAIN            BASE   
4  TORNADO:AGRC:INC_CONSERVATION_AGRICULTURE            BASE   

   evaluate_system_costs  evaluate_transformation_costs  
0                      1                              1  
1                      1                              1  
2                      1                              1  
3                      1                              1  
4                      1                              1

In [26]:
print(
    """
    ++++++++++++++++++++++++++++++++++++++++++++++++++++
    
                    CALCULATE SYSTEM COST

    +++++++++++++++++++++++++++++++++++++++++++++++++++++
    """
)
results_system = cb_calculate_system_costs(cb_input_df, strategy_cost_instructions, cost_factor_names, cb_data, SSP_GLOBAL_list_of_variables, SSP_GLOBAL_list_of_strategies)



    ++++++++++++++++++++++++++++++++++++++++++++++++++++
    
                    CALCULATE SYSTEM COST

    +++++++++++++++++++++++++++++++++++++++++++++++++++++
    
============Evaluating system costs for BASE =================
Cost Factor Loop: BASE vs BASE for cost factor afolu_crop_livestock_production_cost_factors and cost factor function cb_apply_cost_factors
---------Costs for: cb:lvst:lvst_value:livestock_produced:buffalo
                       pop_lvst_buffalo
DESDE cb_difference_between_two_strategies
pop_lvst_buffalo
Valor multiplicador
260.0
---------Costs for: cb:lvst:lvst_value:livestock_produced:cattle_dairy
                       pop_lvst_cattle_dairy
DESDE cb_difference_between_two_strategies
pop_lvst_cattle_dairy
Valor multiplicador
260.0
---------Costs for: cb:lvst:lvst_value:livestock_produced:cattle_nondairy
                       pop_lvst_cattle_nondairy
DESDE cb_difference_between_two_strategies
pop_lvst_cattle_nondairy
Valor multiplicador
260.0
---------Costs

In [27]:
results_system

strategy_code  future_id region  time_period  \
0                             BASE          0   iran            0   
1                             BASE          0   iran            1   
2                             BASE          0   iran            2   
3                             BASE          0   iran            3   
4                             BASE          0   iran            4   
...                            ...        ...    ...          ...   
450859  TORNADO:WASO:INC_RECYCLING          0   iran           31   
450860  TORNADO:WASO:INC_RECYCLING          0   iran           32   
450861  TORNADO:WASO:INC_RECYCLING          0   iran           33   
450862  TORNADO:WASO:INC_RECYCLING          0   iran           34   
450863  TORNADO:WASO:INC_RECYCLING          0   iran           35   

                             difference_variable  difference_value  \
0                               pop_lvst_buffalo          0.000000   
1                               pop_lvst_buffalo          0.000000   
2                               pop_lvst_buffalo          0.000000   
3                               pop_lvst_buffalo          0.000000   
4                               pop_lvst_buffalo          0.000000   
...                                          ...               ...   
450859  gasrecovered_waso_biogas_landfills_tonne      -5908.551031   
450860  gasrecovered_waso_biogas_landfills_tonne      -7196.820504   
450861  gasrecovered_waso_biogas_landfills_tonne      -8625.122363   
450862  gasrecovered_waso_biogas_landfills_tonne     -10180.434162   
450863  gasrecovered_waso_biogas_landfills_tonne     -11851.638958   

                                                variable         value  
0          cb:lvst:lvst_value:livestock_produced:buffalo  0.000000e+00  
1          cb:lvst:lvst_value:livestock_produced:buffalo  0.000000e+00  
2          cb:lvst:lvst_value:livestock_produced:buffalo  0.000000e+00  
3          cb:lvst:lvst_value:livestock_produced:buffalo  0.000000e+00  
4          cb:lvst:lvst_value:livestock_produced:buffalo  0.000000e+00  
...                                                  ...           ...  
450859  cb:waso:fuel_cost:waste_to_energy_value:landfill -1.911590e+06  
450860  cb:waso:fuel_cost:waste_to_energy_value:landfill -2.328383e+06  
450861  cb:waso:fuel_cost:waste_to_energy_value:landfill -2.790481e+06  
450862  cb:waso:fuel_cost:waste_to_energy_value:landfill -3.293670e+06  
450863  cb:waso:fuel_cost:waste_to_energy_value:landfill -3.834354e+06  

[450864 rows x 8 columns]

In [28]:
transformation_cost_definitions.transformation_code.unique()

array(['TX:INEN:FUEL_SWITCH_LO_HEAT', 'TX:INEN:FUEL_SWITCH_HI_HEAT',
       'TX:INEN:SHIFT_FUEL_HEAT', 'TX:INEN:INC_EFFICIENCY_ENERGY',
       'TX:TRNS:SHIFT_FUEL_LIGHT_DUTY', 'TX:TRNS:SHIFT_FUEL_RAIL',
       'TX:TRNS:SHIFT_FUEL_MARITIME', 'TX:TRNS:SHIFT_FUEL_MEDIUM_DUTY',
       'TX:TRNS:INC_EFFICIENCY_ELECTRIC',
       'TX:TRNS:INC_EFFICIENCY_NON_ELECTRIC', 'TX:TRNS:INC_EFFICIENCY',
       'TX:SCOE:INC_EFFICIENCY_APPLIANCE', 'TX:SCOE:SHIFT_FUEL_HEAT',
       'TX:SCOE:DEC_DEMAND_HEAT', 'TX:ENTC:DEC_LOSSES',
       'TX:IPPU:DEC_CLINKER', 'TX:IPPU:BUNDLE_DEC_FGAS',
       'TX:IPPU:DEC_N2O', 'TX:IPPU:DEC_HFCS', 'TX:IPPU:DEC_PFCS',
       'TX:IPPU:DEC_OTHER_FCS', 'TX:FGTV:INC_FLARE', 'TX:FGTV:DEC_LEAKS',
       'TX:WASO:DEC_CONSUMER_FOOD_WASTE', 'TX:CCSQ:INC_CAPTURE',
       'TX:LVST:DEC_ENTERIC_FERMENTATION', 'TX:AGRC:DEC_CH4_RICE',
       'TX:AGRC:DEC_LOSSES_SUPPLY_CHAIN', 'TX:AGRC:INC_PRODUCTIVITY',
       'TX:LVST:INC_PRODUCTIVITY', 'TX:GNRL:DEC_RED_MEAT_CONSUMPTION',
       'TX:LNDU

In [29]:
#calcualte transformation costs

print(
    """
    ++++++++++++++++++++++++++++++++++++++++++++++++++++
    
                    CALCULATE TRANSFORMATION COST

    +++++++++++++++++++++++++++++++++++++++++++++++++++++
    """
)

results_tx = cb_calculate_transformation_costs(cb_input_df, 
                                  strategy_cost_instructions,
                                  strategy2tx, 
                                  transformation_cost_definitions, 
                                  cb_data,
                                  SSP_GLOBAL_list_of_variables, 
                                  SSP_GLOBAL_list_of_strategies)





    ++++++++++++++++++++++++++++++++++++++++++++++++++++
    
                    CALCULATE TRANSFORMATION COST

    +++++++++++++++++++++++++++++++++++++++++++++++++++++
    
The following transformations are in strategy: BASE

Skipping BASE: All of the following transformations [] are not in transformation_cost_definition.
The following transformations are in strategy: TORNADO:AGRC:DEC_CH4_RICE
0: TX:AGRC:DEC_CH4_RICE
1: TX:LNDU:PLUR
Evaluating transformation costs for TORNADO:AGRC:DEC_CH4_RICE which is TORNADO:AGRC:DEC_CH4_RICE vs. BASE for cb:agrc:technical_cost:rice_mgmt:X
============Evaluating transformation costs for TORNADO:AGRC:DEC_CH4_RICE-cb:agrc:technical_cost:rice_mgmt:X
Usaremos la función específica a la estrategia cb_agrc_rice_mgmt
                       area_agrc_crops_rice
The following transformations are in strategy: TORNADO:AGRC:DEC_EXPORTS
0: TX:AGRC:DEC_EXPORTS
1: TX:LNDU:PLUR
Skipping TORNADO:AGRC:DEC_EXPORTS: All of the following transformations ['TX:AGRC:DEC

/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objec

The following transformations are in strategy: TORNADO:FGTV:INC_FLARE
0: TX:LNDU:PLUR
1: TX:FGTV:INC_FLARE
Evaluating transformation costs for TORNADO:FGTV:INC_FLARE which is TORNADO:FGTV:INC_FLARE vs. BASE for cb:fgtv:technical_cost:flaring:X
============Evaluating transformation costs for TORNADO:FGTV:INC_FLARE-cb:fgtv:technical_cost:flaring:X
Usaremos la función específica a la estrategia cb_fgtv_abatement_costs
                       emission_co2e_subsector_total_fgtv
The following transformations are in strategy: TORNADO:INEN:INC_EFFICIENCY_ENERGY_HIGHEST
0: TX:LNDU:PLUR
1: TX:INEN:INC_EFFICIENCY_ENERGY
Evaluating transformation costs for TORNADO:INEN:INC_EFFICIENCY_ENERGY_HIGHEST which is TORNADO:INEN:INC_EFFICIENCY_ENERGY_HIGHEST vs. BASE for cb:inen:technical_cost:efficiency:X
============Evaluating transformation costs for TORNADO:INEN:INC_EFFICIENCY_ENERGY_HIGHEST-cb:inen:technical_cost:efficiency:X
Usaremos la función específica a la estrategia cb_difference_between_two_stra

/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objec

                       emission_co2e_hfcs_ippu_product_use_product_use_ods_other
APLICANDO CB_FRACTION_CHANGE
invert : 1.0
frac_var : ef_ippu_tonne_sf6_per_tonne_production_electronics
strategy_code_tx : TORNADO:IPPU:DEC_HFCS_HIGHEST
strategy_code_base : BASE
diff_var : emission_co2e_hfcs_ippu_product_use_product_use_ods_other
The following transformations are in strategy: TORNADO:IPPU:DEC_N2O
0: TX:LNDU:PLUR
1: TX:IPPU:DEC_N2O
Evaluating transformation costs for TORNADO:IPPU:DEC_N2O which is TORNADO:IPPU:DEC_N2O vs. BASE for cb:ippu:technical_cost:abating_gases:n2o
============Evaluating transformation costs for TORNADO:IPPU:DEC_N2O-cb:ippu:technical_cost:abating_gases:n2o
Usaremos la función específica a la estrategia cb_fraction_change
                       emission_co2e_n2o_ippu_production_paper
APLICANDO CB_FRACTION_CHANGE
invert : 1.0
frac_var : ef_ippu_tonne_n2o_per_tonne_production_electronics
strategy_code_tx : TORNADO:IPPU:DEC_N2O
strategy_code_base : BASE
diff_var : emissio

/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objec

The following transformations are in strategy: TORNADO:LNDU:DEC_DEFORESTATION
0: TX:LNDU:DEC_DEFORESTATION
1: TX:LNDU:PLUR
Skipping TORNADO:LNDU:DEC_DEFORESTATION: All of the following transformations ['TX:LNDU:DEC_DEFORESTATION', 'TX:LNDU:PLUR'] are not in transformation_cost_definition.
The following transformations are in strategy: TORNADO:LNDU:DEC_SOC_LOSS_PASTURES
0: TX:LNDU:DEC_SOC_LOSS_PASTURES
1: TX:LNDU:PLUR
Skipping TORNADO:LNDU:DEC_SOC_LOSS_PASTURES: All of the following transformations ['TX:LNDU:DEC_SOC_LOSS_PASTURES', 'TX:LNDU:PLUR'] are not in transformation_cost_definition.
The following transformations are in strategy: TORNADO:LNDU:INC_REFORESTATION
0: TX:LNDU:INC_REFORESTATION
1: TX:LNDU:PLUR
Skipping TORNADO:LNDU:INC_REFORESTATION: All of the following transformations ['TX:LNDU:INC_REFORESTATION', 'TX:LNDU:PLUR'] are not in transformation_cost_definition.
The following transformations are in strategy: TORNADO:LNDU:INC_SILVOPASTURE
0: TX:LNDU:INC_SILVOPASTURE
1: TX:LND

/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objec

============Evaluating transformation costs for TORNADO:TRNS:SHIFT_FUEL_LIGHT_DUTY-cb:trns:technical_savings:electrification:LDV
Usaremos la función específica a la estrategia cb_difference_between_two_strategies
                       vehicle_distance_traveled_trns_road_light_electricity
DESDE cb_difference_between_two_strategies
vehicle_distance_traveled_trns_road_light_electricity
Valor multiplicador
0.012
The following transformations are in strategy: TORNADO:TRNS:SHIFT_FUEL_MARITIME
0: TX:LNDU:PLUR
1: TX:TRNS:SHIFT_FUEL_MARITIME
Evaluating transformation costs for TORNADO:TRNS:SHIFT_FUEL_MARITIME which is TORNADO:TRNS:SHIFT_FUEL_MARITIME vs. BASE for cb:trns:technical_cost:fuel_switch:maritime
============Evaluating transformation costs for TORNADO:TRNS:SHIFT_FUEL_MARITIME-cb:trns:technical_cost:fuel_switch:maritime
Usaremos la función específica a la estrategia cb_scale_variable_in_strategy
                       mass_distance_traveled_trns_mt_km_water_borne
The following transfo

/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)
/home/tony/ssp/cb_ssp_refac/src/cb_utilities.py:186: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  strategy_cb_table = strategy_cb_table.replace(np.nan, 0.0)


In [30]:
RESULTS_SYSTEMS_PATH = p_utils.build_path([CB_OUTPUT_PATH, "python", "results_system_python.csv"])
RESULTS_TX_SYSTEMS_PATH = p_utils.build_path([CB_OUTPUT_PATH, "python", "results_tx_python.csv"])

In [31]:
#combine the results
results_all = pd.concat([results_system, results_tx], ignore_index = True)

SSP_GLOBAL_list_of_cbvars = results_all["variable"].unique()


#-------------POST PROCESS SIMULATION RESULTS---------------
#Post process interactions among strategies that affect the same variables
postprocess_interactions = pd.read_csv(p_utils.build_path([DEFINITION_FILES_PATH, 'strategy_interaction_definitions.csv']))

results_all_pp = cb_process_interactions(results_all, strategy2tx, postprocess_interactions)

#POST PROCESS TRANSPORT CB ISSUES (These should be addressed properly in the next round of analysis)
#congestion and safety benefits should be 0 in strategies that only make fuel efficiency gains and fuel switching

cond_transport_cb_issues_better_base = (results_all_pp["strategy_code"]=="PFLO:BETTER_BASE") & (results_all_pp["variable"].apply(lambda x : any(k in x for k in ["congestion", "road_safety"])))
cond_transport_cb_issues_supply_side_tech = (results_all_pp["strategy_code"]=="PFLO:SUPPLY_SIDE_TECH") & (results_all_pp["variable"].apply(lambda x : any(k in x for k in ["congestion", "road_safety"])))

results_all_pp.loc[cond_transport_cb_issues_better_base, "value"] = 0.0
results_all_pp.loc[cond_transport_cb_issues_supply_side_tech, "value"] = 0.0

#in ALL, cut the benefits in half to be on the safe side.
cond_cut_ben_in_half_all_plur =  (results_all_pp["strategy_code"]=="PFLO:ALL_PLUR") & (results_all_pp["variable"].apply(lambda x : any(k in x for k in ["congestion", "road_safety"])))
cond_cut_ben_in_half_all_non_stopping_def_plur =  (results_all_pp["strategy_code"]=='PFLO:ALL_NO_STOPPING_DEFORESTATION_PLUR') & (results_all_pp["variable"].apply(lambda x : any(k in x for k in ["congestion", "road_safety"])))

results_all_pp.loc[cond_cut_ben_in_half_all_plur, "value"] *= 0.5 
results_all_pp.loc[cond_cut_ben_in_half_all_non_stopping_def_plur, "value"] *= 0.5 

#POST PROCESS WASO CB ISSUES
#where moving from incineration to landfilling appears to have benefits
#when this move should probably not occur
cond_waso_cb_issue =  (results_all_pp["strategy_code"]=="PFLO:SUPPLY_SIDE_TECH") & (results_all_pp["variable"].apply(lambda x : any(k in x for k in ["cb:waso:technical_cost:waste_management"])))
results_all_pp.loc[cond_waso_cb_issue, "value"] = 0.0


#SHIFT any stray costs incurred from 2015 to 2025 to 2025 and 2035
results_all_pp_before_shift = results_all_pp.copy() #keep copy of earlier results just in case/for comparison
res_pre2025 = results_all_pp.query(f"time_period<{SSP_GLOBAL_TIME_PERIOD_TX_START}")#get the subset of early costs
res_pre2025["variable"] = res_pre2025["variable"] + "_shifted" + (res_pre2025["time_period"]+SSP_GLOBAL_TIME_PERIOD_0).astype(str)#create a new variable so they can be recognized as shifted costs
res_pre2025["time_period"] = res_pre2025["time_period"]+SSP_GLOBAL_TIME_PERIOD_TX_START #shift the time period

results_all_pp = pd.concat([results_all_pp, res_pre2025], ignore_index = True) #paste the results

results_all_pp.loc[results_all_pp["time_period"]<SSP_GLOBAL_TIME_PERIOD_TX_START,'value'] = 0 #set pre-2025 costs to 0


#Write
CB_OUTPUT_FILENAME = p_utils.build_path([CB_OUTPUT_PATH, "cost_benefit_results.csv"])
results_all_pp.to_csv(CB_OUTPUT_FILENAME, index = False)

Resolving Interactions in SCOE :  
No interactions, skipping... BASE
Resolving Interactions in INEN :  
No interactions, skipping... BASE
Resolving Interactions in SCOE :  
No interactions, skipping... TORNADO:AGRC:DEC_CH4_RICE
Resolving Interactions in INEN :  
No interactions, skipping... TORNADO:AGRC:DEC_CH4_RICE
Resolving Interactions in SCOE :  
No interactions, skipping... TORNADO:AGRC:DEC_EXPORTS
Resolving Interactions in INEN :  
No interactions, skipping... TORNADO:AGRC:DEC_EXPORTS
Resolving Interactions in SCOE :  
No interactions, skipping... TORNADO:AGRC:DEC_LOSSES_SUPPLY_CHAIN
Resolving Interactions in INEN :  
No interactions, skipping... TORNADO:AGRC:DEC_LOSSES_SUPPLY_CHAIN
Resolving Interactions in SCOE :  
No interactions, skipping... TORNADO:AGRC:INC_CONSERVATION_AGRICULTURE
Resolving Interactions in INEN :  
No interactions, skipping... TORNADO:AGRC:INC_CONSERVATION_AGRICULTURE
Resolving Interactions in SCOE :  
No interactions, skipping... TORNADO:AGRC:INC_PRODUCTIV

/tmp/ipykernel_47118/3948883160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  res_pre2025["variable"] = res_pre2025["variable"] + "_shifted" + (res_pre2025["time_period"]+SSP_GLOBAL_TIME_PERIOD_0).astype(str)#create a new variable so they can be recognized as shifted costs
/tmp/ipykernel_47118/3948883160.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  res_pre2025["time_period"] = res_pre2025["time_period"]+SSP_GLOBAL_TIME_PERIOD_TX_START #shift the time period
